## 1. Imports

In [1]:
import tensorflow as tf
import tensorflow_datasets as tfds
import numpy
tf.enable_eager_execution()
import magenta.models
import magenta.music as mm
import copy


In [2]:
import magenta.models.music_vae.configs as configs
from magenta.models.music_vae.data import GrooveConverter
# from magenta.models.music_vae.music_vae_train import _get_input_tensors

In [3]:
from magenta.models.music_vae import configs
from magenta.models.music_vae import data
import tensorflow as tf
from tensorflow.contrib import training as contrib_training

In [4]:
from magenta.music.midi_io import midi_file_to_note_sequence

from magenta.pipelines.drum_pipelines import extract_drum_tracks

from magenta.music.drums_lib import DrumTrack

from magenta.music.sequences_lib import is_absolute_quantized_sequence
from magenta.music.sequences_lib import quantize_note_sequence
from magenta.music.sequences_lib import quantize_note_sequence_absolute


## 2. Load groove dataset with info

In [30]:
tfdataset,info = tfds.load(name = "groove/2bar-midionly",split=tfds.Split.VALIDATION,with_info = True)
# tfdataset is an iterable object,generates an iterator when passed to an iter() function
dataset_2bar = tfds.as_numpy(tfdataset)
#Converts a tf.data.Dataset to an iterable of NumPy arrays.

In [15]:
# it = iter(tfdataset)
# print(next(it))
count=0
for x in tfdataset:
    count +=1
print(count)

2252


In [7]:
for example in tfdataset.take(1):
    a,b,c  = example['bpm'],example['midi'],example['style']
    print(a,b,c)
   

tf.Tensor(180, shape=(), dtype=int32) tf.Tensor(b"MThd\x00\x00\x00\x06\x00\x01\x00\x02\x01\xe0MTrk\x00\x00\x00\x19\x00\xffQ\x03\x05\x16\x15\x00\xffX\x04\x04\x02\x18\x08\x00\xffY\x02\x00\x00\x01\xff/\x00MTrk\x00\x00\x00\xe0\x00\xff\x03\nMidi Drums\x00\xc9\x00\x00\xb9\x04$\x1e\x04\x1f+\x04\x1a6\x04\x15@\x04\x10\x14\x99$\x7f,\xb9\x04\x0ce\x99$\x00\x81\x067\x7f\x04&\x7f\x81\x0c7\x00\x05&\x00\x08\xb9\x04\x07\x81P\x04\x0bd\x99$\x7f\x1a\xb9\x04\x0c\x01\x99\x1a\x7fl\xb9\x04\x07\x0b\x99$\x00\x1a\x1a\x00\x82%(\x7f\r\xb9\x04\x04\x00\x99\x1a\x7f\x81\x05(\x00\x0e\x1a\x00\\$\x7f\x81\x12$\x00o\xb9\x04\x04\x00\x99\x1a\x7f\x81\x12\x1a\x00'$\x7fJ\xb9\x04\x00H\x99$\x00|(\x7f\x0f\xb9\x04\x02\x00\x99\x1a\x7fM\xb9\x04\x005\x99(\x00\x10\x1a\x00\x81?\xb9\x04\x04M\x04\tD\x04\t\x00\x99\x1a\x7f\x11$\x7fT\xb9\x04\x04-\x99\x1a\x00\x10$\x00\x825\xb9\x04\x04\x00\x99\x1a\x7f\t(|\x81\t\x1a\x00\x07(\x00S$\x7f\x81\x11$\x00b\xb9\x04\x07\x01\xff/\x00", shape=(), dtype=string) {'primary': <tf.Tensor: id=130, shape=(), dtyp

In [31]:
count = 0
for ex in dataset_2bar:
#      count +=1
     print(ex)
# print(count)

{'bpm': 180, 'drummer': 5, 'id': b'drummer6/session3/5:000:001:002:003:004:005:006:007:008:009:010:011:012:013', 'midi': b"MThd\x00\x00\x00\x06\x00\x01\x00\x02\x01\xe0MTrk\x00\x00\x00\x19\x00\xffQ\x03\x05\x16\x15\x00\xffX\x04\x04\x02\x18\x08\x00\xffY\x02\x00\x00\x01\xff/\x00MTrk\x00\x00\x00\xe0\x00\xff\x03\nMidi Drums\x00\xc9\x00\x00\xb9\x04$\x1e\x04\x1f+\x04\x1a6\x04\x15@\x04\x10\x14\x99$\x7f,\xb9\x04\x0ce\x99$\x00\x81\x067\x7f\x04&\x7f\x81\x0c7\x00\x05&\x00\x08\xb9\x04\x07\x81P\x04\x0bd\x99$\x7f\x1a\xb9\x04\x0c\x01\x99\x1a\x7fl\xb9\x04\x07\x0b\x99$\x00\x1a\x1a\x00\x82%(\x7f\r\xb9\x04\x04\x00\x99\x1a\x7f\x81\x05(\x00\x0e\x1a\x00\\$\x7f\x81\x12$\x00o\xb9\x04\x04\x00\x99\x1a\x7f\x81\x12\x1a\x00'$\x7fJ\xb9\x04\x00H\x99$\x00|(\x7f\x0f\xb9\x04\x02\x00\x99\x1a\x7fM\xb9\x04\x005\x99(\x00\x10\x1a\x00\x81?\xb9\x04\x04M\x04\tD\x04\t\x00\x99\x1a\x7f\x11$\x7fT\xb9\x04\x04-\x99\x1a\x00\x10$\x00\x825\xb9\x04\x04\x00\x99\x1a\x7f\t(|\x81\t\x1a\x00\x07(\x00S$\x7f\x81\x11$\x00b\xb9\x04\x07\x01\xff/\x00

{'bpm': 157, 'drummer': 0, 'id': b'drummer1/session2/1:000:001:002:003:004:005:006:007:008:009:010:011:012:013:014:015:016:017:018:019:020:021:022:023:024:025:026:027:028:029:030:031:032:033:034:035:036:037:038:039:040:041:042:043:044:045:046:047:048:049:050:051:052:053:054:055:056:057:058:059:060:061:062:063:064:065:066:067:068:069:070:071:072:073:074:075:076:077:078:079:080:081:082:083:084:085:086:087:088:089:090:091:092:093:094:095:096:097:098:099:100:101:102:103:104:105:106:107:108:109:110:111:112:113:114:115:116:117:118', 'midi': b'MThd\x00\x00\x00\x06\x00\x01\x00\x02\x01\xe0MTrk\x00\x00\x00\x19\x00\xffQ\x03\x05\xd4\xd5\x00\xffX\x04\x03\x02\x18\x08\x00\xffY\x02\x00\x00\x01\xff/\x00MTrk\x00\x00\x00\xc3\x00\xff\x03\nMidi Drums\x00\xc9\x00\x00\xb9\x04Z\x81k\x04Z\x00\x99*&\x81\x00*\x00Z$7\x18\xb9\x04Z\x00\x99*)f$\x00\x19*\x00o%B\x08\xb9\x04Z\x00\x99*4v%\x00\t*\x00e\xb9\x04Z\x00\x99*)\x06$7z*\x00\x05$\x00^\xb9\x04Z\x00\x99*+\x81\x00*\x00p%N\x0c\xb9\x04Z\x01\x99*<r%\x00\x0c*\x00l\xb9\x0

{'bpm': 89, 'drummer': 4, 'id': b'drummer5/session1/4:000:001:002:003:004:005:006:007:008:009:010:011:012:013:014:015:016:017:018:019:020:021:022:023:024:025:026:027:028:029:030:031:032:033:034:035:036:037:038:039:040:041:042:043:044:045:046:047:048:049:050:051:052:053:054:055:056:057:058:059:060:061:062:063:064', 'midi': b'MThd\x00\x00\x00\x06\x00\x01\x00\x02\x01\xe0MTrk\x00\x00\x00\x19\x00\xffQ\x03\nIm\x00\xffX\x04\x04\x02\x18\x08\x00\xffY\x02\x00\x00\x01\xff/\x00MTrk\x00\x00\x03\x0f\x00\xff\x03\nMidi Drums\x00\xc9\x00\x00\xb9\x04O\x17\x04Z?\x99&0\r\xb9\x04L#\x04\x00\x18\x99&\x00-&#%\xb9\x04 \n\x99,#\x16\xb9\x04Z\x03\x99&\x00 \xb9\x04B\n\x99&G\x04,\x00\x0f$\x16\x1a\xb9\x04I\x1b\x99&\x00\x08\xb9\x04W\x0b\x99$\x00#\xb9\x04K\x04\x99+C#$#\r\xb9\x04Z\x18\x99+\x00#$\x00\x0b\xb9\x04N\x01\x99&\x19%\xb9\x04\x00#\x99&\x00-&c\x17\xb9\x04\x10\n\x99,4\x16\xb9\x04Z\x11\x99&\x00\x1d\xb9\x04E\x04\x99,\x00\x11& \x0e$\r\x01\xb9\x04+%\x04H\x14\x99&\x00\x0b\xb9\x04W\x03\x99$\x00\x1d\xb9\x04?\x04\x99&Q\x

{'bpm': 142, 'drummer': 6, 'id': b'drummer7/session2/96:000:001:002:003:004:005:006:007:008:009:010:011:012:013:014:015:016:017:018:019:020:021:022:023:024:025:026:027:028:029:030:031:032:033:034', 'midi': b'MThd\x00\x00\x00\x06\x00\x01\x00\x02\x01\xe0MTrk\x00\x00\x00\x19\x00\xffQ\x03\x06r\x87\x00\xffX\x04\x04\x02\x18\x08\x00\xffY\x02\x00\x00\x01\xff/\x00MTrk\x00\x00\x01\x0f\x00\xff\x03\nMidi Drums\x00\xc9\x00\x00\xb9\x04Z\x81d\x04Z\x01\x99*,l\xb9\x04Z\x00\x99*\x00\x00*/\x06*\x00c\xb9\x04Z\x00\x99\x16\x7fs\x16\x00r\xb9\x04Z\x00\x99*1\x18$CZ*\x00\x18$\x00o&\x7f\t\xb9\x04Z\x00\x99\x16\x7fi&\x00\n\x16\x00\x81\x02\xb9\x04Z\x01\x99* s*\x00\x01\xb9\x04Z\x00\x99*/s\xb9\x04Z\x00\x99\x16\x7f\x00*\x00s\x16\x00\x81\x05\xb9\x04Z\x01\x99*%r\xb9\x04Z\x00\x99\x16T\x00*\x00t\x16\x00\r\xb9\x04Z\x01\x99\x16\x7fr\x16\x00x\xb9\x04Z\x00\x99*%s*\x00\x17\xb9\x04Z\x01\x99\x16\x1cl\xb9\x04Z\x00\x99\x16\x00\x00\x16\x7f\x07\x16\x00\x07$Fs$\x00[\xb9\x04Z\x01\x99*!r*\x00_&|\x14\xb9\x04Z\x00\x99\x16\x7f^&\x00\x16\x

{'bpm': 133, 'drummer': 4, 'id': b'drummer5/session2/22:000:001:002:003:004:005:006:007:008:009:010:011:012:013:014:015:016:017:018:019:020:021:022:023:024:025:026:027:028:029', 'midi': b'MThd\x00\x00\x00\x06\x00\x01\x00\x02\x01\xe0MTrk\x00\x00\x00\x19\x00\xffQ\x03\x06\xe27\x00\xffX\x04\x04\x02\x18\x08\x00\xffY\x02\x00\x00\x01\xff/\x00MTrk\x00\x00\x02\x8e\x00\xff\x03\nMidi Drums\x00\xc9\x00\x00\xb9\x04N\x05\x04Z\x05\x99$,=$\x00\x00$\x0e\x03\xb9\x04)#\x04\x00\t\x99$\x00\x10&@\\\xb9\x04M\x00\x99,P\t&\x00\x00&+\x06&\x00\x13\xb9\x04ZJ\x99,\x00\x16\xb9\x04;\x12\x99(j\x0c\xb9\x04&1\x04P\x01\x99,\x19!\xb9\x04Z\x04\x99(\x00\x00({\t(\x00\x06$&7\xb9\x04*\x00\x99,\x00&\xb9\x04\x00\r\x99$\x00\x11&)O\xb9\x04N\x00\x99,U\x12(\x7f\x0b&\x00\x05\xb9\x04ZJ\x99,\x00\n\xb9\x04K\x07\x99(\x00\x18&7\x08\xb9\x049,\x04V\x1f\x04Z\x18\x99&\x00\n&+\x15$(\x1b\xb9\x04*"\x04\x00\x19\x99&\x00\t(}\r$\x00D\xb9\x04L\x00\x99,W\x1a(\x00\x08\xb9\x04Z\t\x99&.@,\x00!\xb9\x04D\n\x99&\x00\x14&7#\xb9\x04M%\x04Z#\x99&\x00\x06(\x7

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



## 3.0 To have a look at all available features in feature dictionary

In [14]:
print(info.features)

FeaturesDict({
    'bpm': Tensor(shape=(), dtype=tf.int32),
    'drummer': ClassLabel(shape=(), dtype=tf.int64, num_classes=10),
    'id': Tensor(shape=(), dtype=tf.string),
    'midi': Tensor(shape=(), dtype=tf.string),
    'style': FeaturesDict({
        'primary': ClassLabel(shape=(), dtype=tf.int64, num_classes=18),
        'secondary': Tensor(shape=(), dtype=tf.string),
    }),
    'time_signature': ClassLabel(shape=(), dtype=tf.int64, num_classes=5),
    'type': ClassLabel(shape=(), dtype=tf.int64, num_classes=2),
})


In [15]:
tfdataset.element_spec

{'bpm': TensorSpec(shape=(), dtype=tf.int32, name=None),
 'drummer': TensorSpec(shape=(), dtype=tf.int64, name=None),
 'id': TensorSpec(shape=(), dtype=tf.string, name=None),
 'midi': TensorSpec(shape=(), dtype=tf.string, name=None),
 'style': {'primary': TensorSpec(shape=(), dtype=tf.int64, name=None),
  'secondary': TensorSpec(shape=(), dtype=tf.string, name=None)},
 'time_signature': TensorSpec(shape=(), dtype=tf.int64, name=None),
 'type': TensorSpec(shape=(), dtype=tf.int64, name=None)}

## 4.0 Load the groovae Configuration object
* config_map: Dictionary mapping configuration name to config object
* passed as an argument to run() while training the VAE

In [11]:
config_2_bar = configs.CONFIG_MAP['groovae_2bar_humanize']

In [12]:
print(config_2_bar)
# repr(config_2_bar)
# dir(config_2_bar)
# print(config_2_bar.hparams)
config_2_bar.values()

Config(model=<magenta.models.music_vae.base_model.MusicVAE object at 0x000001C1C5634F48>, hparams=HParams([('batch_size', 512), ('beta_rate', 0.0), ('clip_mode', 'global_norm'), ('conditional', True), ('dec_rnn_size', [256, 256]), ('decay_rate', 0.9999), ('dropout_keep_prob', 0.3), ('enc_rnn_size', [512]), ('free_bits', 48), ('grad_clip', 1.0), ('grad_norm_clip_to_zero', 10000), ('learning_rate', 0.001), ('max_beta', 0.2), ('max_seq_len', 32), ('min_learning_rate', 1e-05), ('residual_decoder', False), ('residual_encoder', False), ('sampling_rate', 0.0), ('sampling_schedule', 'constant'), ('use_cudnn', False), ('z_size', 256)]), note_sequence_augmenter=None, data_converter=<magenta.models.music_vae.data.GrooveConverter object at 0x000001C1C5634F88>, train_examples_path=None, eval_examples_path=None, tfds_name='groove/2bar-midionly')


OrderedDict([('model',
              <magenta.models.music_vae.base_model.MusicVAE at 0x1c1c5634f48>),
             ('hparams',
              HParams([('batch_size', 512), ('beta_rate', 0.0), ('clip_mode', 'global_norm'), ('conditional', True), ('dec_rnn_size', [256, 256]), ('decay_rate', 0.9999), ('dropout_keep_prob', 0.3), ('enc_rnn_size', [512]), ('free_bits', 48), ('grad_clip', 1.0), ('grad_norm_clip_to_zero', 10000), ('learning_rate', 0.001), ('max_beta', 0.2), ('max_seq_len', 32), ('min_learning_rate', 1e-05), ('residual_decoder', False), ('residual_encoder', False), ('sampling_rate', 0.0), ('sampling_schedule', 'constant'), ('use_cudnn', False), ('z_size', 256)])),
             ('note_sequence_augmenter', None),
             ('data_converter',
              <magenta.models.music_vae.data.GrooveConverter at 0x1c1c5634f88>),
             ('train_examples_path', None),
             ('eval_examples_path', None),
             ('tfds_name', 'groove/2bar-midionly')])

In [13]:
def _get_input_tensors(dataset, config):
  """Get input tensors from dataset."""
#   import pdb
#   pdb.set_trace()
  batch_size = config.hparams.batch_size
  iterator = dataset.make_one_shot_iterator()
  (input_sequence, output_sequence, control_sequence,
   sequence_length) = iterator.get_next()
  input_sequence.set_shape(
      [batch_size, None, config.data_converter.input_depth])
  output_sequence.set_shape(
      [batch_size, None, config.data_converter.output_depth])
  if not config.data_converter.control_depth:
    control_sequence = None
  else:
    control_sequence.set_shape(
        [batch_size, None, config.data_converter.control_depth])
  sequence_length.set_shape([batch_size] + sequence_length.shape[1:].as_list())
  return {
      'input_sequence': input_sequence,
      'output_sequence': output_sequence,
      'control_sequence': control_sequence,
      'sequence_length': sequence_length
  }

In [14]:
def get_dataset(
    config,
    num_threads=1,
    tf_file_reader=tf.data.TFRecordDataset,
    is_training=False,
    cache_dataset=True):
  """Get input tensors from dataset for training or evaluation.

  Args:
    config: A Config object containing dataset information.
    num_threads: The number of threads to use for pre-processing.
    tf_file_reader: The tf.data.Dataset class to use for reading files.
    is_training: Whether or not the dataset is used in training. Determines
      whether dataset is shuffled and repeated, etc.
    cache_dataset: Whether to cache the dataset in memory for improved
      performance.

  Returns:
    A tf.data.Dataset containing input, output, control, and length tensors.

  Raises:
    ValueError: If no files match examples path.
  """
  batch_size = config.hparams.batch_size
  examples_path = (
      config.train_examples_path if is_training else config.eval_examples_path)
  note_sequence_augmenter = (
      config.note_sequence_augmenter if is_training else None)
  data_converter = config.data_converter
  data_converter.set_mode('train' if is_training else 'eval')

  if examples_path:
    tf.logging.info('Reading examples from file: %s', examples_path)
    num_files = len(tf.gfile.Glob(examples_path))
    if not num_files:
      raise ValueError(
          'No files were found matching examples path: %s' %  examples_path)
    files = tf.data.Dataset.list_files(examples_path)
    dataset = files.apply(
        contrib_data.parallel_interleave(
            tf_file_reader, cycle_length=num_threads, sloppy=is_training))
  elif config.tfds_name:
    tf.logging.info('Reading examples from TFDS: %s', config.tfds_name)
    dataset = tfds.load(
        config.tfds_name,
        split=tfds.Split.TRAIN if is_training else tfds.Split.VALIDATION,
        shuffle_files=is_training,
        try_gcs=False)
    def _tf_midi_to_note_sequence(ex):
      return tf.py_function(
          lambda x: [mm.midi_to_note_sequence(x.numpy()).SerializeToString()],
          inp=[ex['midi']],
          Tout=tf.string,
          name='midi_to_note_sequence')
    dataset = dataset.map(
        _tf_midi_to_note_sequence,
        num_parallel_calls=tf.data.experimental.AUTOTUNE)
  else:
    raise ValueError(
        'One of `config.examples_path` or `config.tfds_name` must be defined.')

  def _remove_pad_fn(padded_seq_1, padded_seq_2, padded_seq_3, length):
    if length.shape.ndims == 0:
      return (padded_seq_1[0:length], padded_seq_2[0:length],
              padded_seq_3[0:length], length)
    else:
      # Don't remove padding for hierarchical examples.
      return padded_seq_1, padded_seq_2, padded_seq_3, length

  if note_sequence_augmenter is not None:
    dataset = dataset.map(note_sequence_augmenter.tf_augment)
  dataset = (dataset
             .map(data_converter.tf_to_tensors,
                  num_parallel_calls=tf.data.experimental.AUTOTUNE)
             .flat_map(lambda *t: tf.data.Dataset.from_tensor_slices(t))
             .map(_remove_pad_fn,
                  num_parallel_calls=tf.data.experimental.AUTOTUNE))
  if cache_dataset:
    dataset = dataset.cache()
  if is_training:
    dataset = dataset.shuffle(buffer_size=10 * batch_size).repeat()

  dataset = dataset.padded_batch(
      batch_size,
      dataset.output_shapes,
      drop_remainder=True).prefetch(tf.data.experimental.AUTOTUNE)

  return dataset


In [68]:
tensordata = get_dataset(config_2_bar)
tensordata2 = _get_input_tensors(tensordata,config_2_bar)

INFO:tensorflow:Reading examples from TFDS: groove/2bar-midionly


INFO:tensorflow:Reading examples from TFDS: groove/2bar-midionly


In [48]:
# dir(tensordata)
# dir(tensordata2)

### 5. The function we have to learn is the mapping between output_sequence and input_sequence

* Each tensor is a shape of 512x32x27. A single example will be of shape 1x32x27.

* 32 is the length of the time steps and represents two bars(16 steps = 1 bar)

* 27 = 9x3
    * the first 9 features are the pitches of the drums. 1 represents a hit(SCORE)
    * the next 9 features are the velocity features(VELOCITY)
    * the next 9 features are the offset features(OFFSET)
    
* The input_sequence has only the score and velocity and offset are set to 0

* The model upon training will learn the mapping to the output_sequence which is the ground truth

In [76]:
print(tensordata2['output_sequence'][1][:][:]-tensordata2['input_sequence'][1][:][:])

tf.Tensor(
[[ 0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.96850395  0.          0.
   0.          0.          0.          0.          0.          0.
   0.9         0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.          0.          0.          0.          0.          0.
   0.         

In [77]:
# print(tensordata2)
# print(tensordata2)

### 6.Help Required to:
    * feed the tensors into a language model like the Music Transformer
    * Creating an embedding of the 27 shape of the tensor for each timestep to create a vocabulary
    * decoding this sequence back to the tensore
    * decoding the tensors to recreate MIDI files

* This is a refrence point:
https://github.com/jason9693/MusicTransformer-tensorflow2.0

* this is the paper for the above repo: https://arxiv.org/pdf/1809.04281.pdf